# Assignment #5 Solutions
#### A good practice in applications is to use column aliases to give result set columns descriptive names.

In [1]:
from data201 import db_connection, df_query

In [2]:
conn = db_connection(config_file = 'ZAGI-sales.ini')
cursor = conn.cursor()

### **1.** Display the region ID, region name, and number of stores in the region for all regions.

In [3]:
df_query(conn,
    """
    SELECT r.region_id AS 'Region ID',
           r.region_name AS 'Region name', 
           COUNT(*) AS 'Region store count'
    FROM region r
    JOIN store s
      ON s.region_id = r.region_id
    GROUP BY r.region_id, r.region_name
    """
)

Region ID  Region name  Region store count
0         C  Chicagoland                   2
1         T     Tristate                   1

### **2.** For each product category, display the category ID, category name, and average price of a product in the category.

In [4]:
df_query(conn,
    """
    SELECT c.category_id AS 'Category ID', 
           c.category_name AS 'Category name', 
           AVG(p.product_price) AS 'Average product price'
    FROM product p, category c
    WHERE p.category_id = c.category_id
    GROUP BY c.category_id, c.category_name
    """
)

Category ID Category name  Average product price
0          CP       Camping             166.666667
1          FW      Footwear              58.333333

### **3.** For each product category, display the category ID and the total number of items purchased in the category.

In [5]:
df_query(conn,
    """
    SELECT p.category_id AS 'Category ID', 
           SUM(s.no_of_items) AS 'Total products purchased'
    FROM sold_via s
    JOIN product p USING (product_id)
    GROUP BY p.category_id
    """
)

Category ID  Total products purchased
0          CP                       5.0
1          FW                      13.0

### **4.** Display the TID and the total number of items (of all products) sold within the transaction for all sales transactions whose total number of items (of all products) sold within the transaction is greater than five.

In [6]:
df_query(conn,
    """
    SELECT tid AS 'Tranaction ID', 
           SUM(no_of_items) AS 'Total products sold > 5'
    FROM sold_via
    GROUP BY tid
    HAVING SUM(no_of_items) > 5
    """
)

Tranaction ID  Total products sold > 5
0          T333                      6.0
1          T555                      7.0

### **5.** Display the product IDs and the product names of the cheapest products.
#### We can't simply sort the procts by price in ascending order and then use `LIMIT 1` to pick the product at the top of the order. There can be more than one product with the lowest price. Therefore, we need the nested `SELECT` to first determine the lowest price, and the outer `SELECT` matches products to that price.

In [7]:
df_query(conn,
    """
    SELECT product_id AS 'Product ID', 
           product_name AS 'Cheapest products'
    FROM product
    WHERE product_price = (SELECT MIN(product_price)
                           FROM product)
    """
)

Product ID Cheapest products
0        3X3         Cosy Sock

### **6.** Display the product ID for the product that has been sold the most (i.e., that has been sold in the highest quantity).

#### The following query works with most versions of SQL. The nested SELECT in the HAVING clause selects the highest number of product sales.

In [8]:
df_query(conn,
    """
    SELECT product_id AS 'Highest selling products'
    FROM sold_via
    GROUP BY product_id
    HAVING SUM(no_of_items) = (SELECT MAX(SUM(no_of_items))
                               FROM sold_via
                               GROUP BY product_id)
    """
)

DatabaseError: Execution failed on sql '
    SELECT product_id AS 'Highest selling products'
    FROM sold_via
    GROUP BY product_id
    HAVING SUM(no_of_items) = (SELECT MAX(SUM(no_of_items))
                               FROM sold_via
                               GROUP BY product_id)
    ': 1111 (HY000): Invalid use of group function

#### Could the problem here be with the nested `SELECT`?

In [9]:
df_query(conn,
    """
    SELECT MAX(SUM(no_of_items))
    FROM sold_via
    GROUP BY product_id|
    """
)

DatabaseError: Execution failed on sql '
    SELECT MAX(SUM(no_of_items))
    FROM sold_via
    GROUP BY product_id|
    ': 1064 (42000): You have an error in your SQL syntax; check the manual that corresponds to your MySQL server version for the right syntax to use near '' at line 3

#### Yes, that's where the problem is. MySQL apparently doesn't like the combination MAX(SUM(no_of_items)) in the SELECT. No, I don't know why MySQL is missing certain language features. 

#### So let's find the highest number of product sales in another way. First, what are the number of sales per product?

In [10]:
# Query A

df_query(conn,
    """
    SELECT product_id AS 'Product ID', 
           SUM(no_of_items) AS 'Total number of sales'
    FROM sold_via
    GROUP BY product_id
    """
)

Product ID  Total number of sales
0        1X1                    2.0
1        2X2                    3.0
2        3X3                    5.0
3        4X4                    5.0
4        5X5                    2.0
5        6X6                    1.0

#### We're going to nest the above `SELECT` in an outer `SELECT`'s `FROM` clause. A `FROM` cause must contain table names. The nested `SELECT` will have the role of a **virtual table**, and so we'll give it the name `total_sales_table`. Also, we'll give its total number of sales column the valid column name `total_sales`. Then the outer `SELECT` in Query C below will be able to select the `MAX` from the `total_sales` column of the virtual table.

In [11]:
# Query B

df_query(conn,
    """
    SELECT MAX(total_sales) AS 'Highest total sales'
    FROM (SELECT SUM(no_of_items) AS total_sales
          FROM sold_via
          GROUP BY product_id) 
              AS total_sales_table
    """
)

Highest total sales
0                  5.0

#### Another way to obtain the highest product sales *number* is to sort the result of Query A in descending order and then take the top row.

#### Note that if you rename a column with an alias, the other parts of the query must use that alias, as in the `ORDER BY`.

#### **WARNING:** `ORDER BY` fails to sort if the alias is a string.

In [12]:
# Query B'

df_query(conn,
    """
    SELECT SUM(no_of_items) AS highest_total_sales
    FROM sold_via
    GROUP BY product_id
    ORDER BY highest_total_sales DESC
    LIMIT 1
    """
)

highest_total_sales
0                  5.0

#### In either case, since we have a `SELECT` command that returns the highest sales, we can use it to select the products whose total sales matches the highest sales. We nest the `SELECT` command in the `HAVING` clause of the outer `SELECT`.

#### Query C below combines Query A and Query B.

In [13]:
# Query C = combined Query A and Query B

df_query(conn,
    """
    SELECT product_id AS 'Highest selling products'
    FROM sold_via
    GROUP BY product_id
    HAVING SUM(no_of_items) = 
        (SELECT MAX(total_sales) AS highest_sales
         FROM (SELECT sum(no_of_items) AS total_sales
               FROM sold_via
               GROUP BY product_id) 
                   AS total_sales_table)
    ORDER BY product_id
    """
)

Highest selling products
0                      3X3
1                      4X4

#### Query C' below combines Query A and Query B'.

In [14]:
# Query C' = combined Query A and Query B'

df_query(conn,
    """
    SELECT product_id AS 'Highest selling products'
    FROM sold_via
    GROUP BY product_id
    HAVING SUM(no_of_items) = 
        (SELECT SUM(no_of_items) AS highest_sales
         FROM sold_via
         GROUP BY product_id
         ORDER BY highest_sales DESC
         LIMIT 1)
    ORDER BY product_id
    """
)

Highest selling products
0                      3X3
1                      4X4

#### **7.** Rewrite the following query using a join instead of the nested query. Your rewritten query should produce the same results.

#### _For each product that has more than three items sold within all sales transactions, retrieve the product ID, product name, and product price._

In [15]:
# Nested query

df_query(conn,
    """
    SELECT product_id AS 'Product ID',
           product_name AS 'Product name', 
           product_price AS 'Price for more than three sold'
    FROM product
    WHERE product_id IN (SELECT product_id
                         FROM sold_via
                         GROUP BY product_id
                         HAVING SUM(no_of_items) > 3)
    """
)

Product ID Product name  Price for more than three sold
0        3X3    Cosy Sock                            15.0
1        4X4    Dura Boot                            90.0

In [16]:
# Rewritten using JOIN

df_query(conn,
    """
    SELECT product_id AS 'Product ID',
           product_name AS 'Product name', 
           product_price AS 'Price for more than three sold'
    FROM product
    JOIN sold_via USING (product_id)
    GROUP BY product_id, product_name, product_price
    HAVING SUM(no_of_items) > 3
    """
)

Product ID Product name  Price for more than three sold
0        3X3    Cosy Sock                            15.0
1        4X4    Dura Boot                            90.0

#### **8.** Rewrite the following query using a join instead of the nested query. Your rewritten query should produce the same results.

#### _For each product whose items were sold in more than one sales transaction, retrieve the product id, product name and product price._

In [17]:
# Nested query

df_query(conn,
    """
    SELECT product_id AS 'Product ID',
           product_name AS 'Product name', 
           product_price AS 
               'Prices of products sold in more than one transaction'
    FROM product
    WHERE product_id IN (SELECT product_id
                         FROM sold_via
                         GROUP BY product_id
                         HAVING COUNT(product_id) > 1)
    """
)

Product ID Product name  \
0        1X1      Zzz Bag   
1        2X2    Easy Boot   
2        4X4    Dura Boot   

   Prices of products sold in more than one transaction  
0                                              100.0     
1                                               70.0     
2                                               90.0

In [18]:
# Rewritten using JOIN

df_query(conn,
    """
    SELECT product_id AS 'Product ID',
           product_name AS 'Product name', 
           product_price AS 
               'Prices of products sold in more than one transaction'
    FROM product
    JOIN sold_via USING (product_id)
    GROUP BY product_id, product_name, product_price
    HAVING COUNT(tid) > 1
    """
)

Product ID Product name  \
0        1X1      Zzz Bag   
1        2X2    Easy Boot   
2        4X4    Dura Boot   

   Prices of products sold in more than one transaction  
0                                              100.0     
1                                               70.0     
2                                               90.0

In [19]:
cursor.close()
conn.close()